<a href="https://colab.research.google.com/github/dla9944/God_damn_deeplearning/blob/master/NLP_test_Shakespear_RNN_ver4.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 셰익스피어 데이터 : 중세 영어 말투 학습

In [35]:
import string
all_chars = string.printable
vocab_size = len(all_chars)
vocab_dict = dict((c,i) for (i,c) in enumerate(all_chars))

# Reference
* https://github.com/karpathy/char-rnn/tree/master/data/tinyshakespeare
* 원데이터 작성자는 TESLA, OpenAi Director 출신 사이언티스트로 현재는 유튜브에서도 연구를 만나볼수 있습니다.(https://www.youtube.com/@AndrejKarpathy)

In [36]:
def str2ints(s, vocab_dict):
    return [vocab_dict[c] for c in s]

In [37]:
def ints2str(x, vocab_array):
    return "".join([vocab_array[i] for i in x])

In [38]:
from google.colab import files
uploaded = files.upload()

Saving input.txt to input (1).txt


In [39]:
import torch
from torch import nn, optim
from torch.utils.data import Dataset, DataLoader, TensorDataset
import tqdm

In [40]:
class ShakespeareDataset(Dataset):
   def __init__(self, path, chunk_size = 200):
       data = str2ints(open(path).read().strip(), vocab_dict)

       data = torch.tensor(data, dtype = torch.int64).split(chunk_size)

       if len(data[-1]) < chunk_size:
          data = data[:-1]
       self.data = data
       self.n_chunks = len(self.data)

   def __len__(self):
       return self.n_chunks
   def __getitem__(self, idx):
       return self.data[idx]

In [41]:
ds = ShakespeareDataset('/content/input.txt', chunk_size = 200)

loader = DataLoader(ds, batch_size = 32, shuffle = True, num_workers = 4)

In [42]:
from tqdm.notebook import tqdm
from torch.optim.adam import Adam

USE_CUDA = torch.cuda.is_available()
device = torch.device("cuda" if USE_CUDA else "cpu")
print(f'running in {device}')

running in cuda


In [43]:
# model 신경망
class SequenceGenerationNet(nn.Module):

   def __init__(self, num_embeddings, embedding_dim = 50, hidden_size = 50, num_layers = 1, dropout = 0.2):
       super().__init__()
       self.emb = nn.Embedding(num_embeddings, embedding_dim)
       self.lstm = nn.LSTM(embedding_dim, hidden_size, num_layers, batch_first = True,
                           dropout=dropout)
       self.linear = nn.Linear(hidden_size, num_embeddings)
   def forward(self, x, h0 = None):
       x = self.emb(x)
       x, h = self.lstm(x, h0)
       x = self.linear(x)
       return x, h

In [44]:
# 문장 생성하는 함수

def generate_seq(net, start_phrase = 'The King said ', length = 200, temperature = 0.8, device = device):
    # 평가모드
    net.eval()
    result = []

    start_tensor = torch.tensor(str2ints(start_phrase, vocab_dict),
                                dtype = torch.int64).to(device)
    # 선두에 batch 차원
    x0 = start_tensor.unsqueeze(0)

    # RNN을 통해서 출력과 새로운 내부 상태 추출
    o, h = net(x0)

    # 출력을 확률로 변환 (exp() =지수함수)
    out_dist = o[:, -1].view(-1).exp()

    # 확률로부터 실제 문자의 인덱스 샘플링
    top_i = torch.multinomial(out_dist, 1)[0]

    # save
    result.append(top_i)

    # 결과는 RNN에 투입
    for i in range(length):
        inp = torch.tensor([[top_i]], dtype = torch.int64)
        inp = inp.to(device)
        o, h = net(inp, h)
        out_dist = o.view(-1).exp()
        top_i = torch.multinomial(out_dist,1)[0]
        result.append(top_i)

    # 시작 문자열과 생성된 문자열을 모아서 반환
    return start_phrase + ints2str(result, all_chars)

In [45]:
from statistics import mean
from torch.optim.adam import Adam

In [22]:
# 모델 훈련용 함수

net = SequenceGenerationNet(vocab_size, 20, 50, num_layers = 2, dropout = 0.1)
net.to(device)

# optimizer function = 아담
optim = optim.Adam(net.parameters())

# loss function = 크로스 엔트로피
loss_function = nn.CrossEntropyLoss()

AttributeError: ignored

In [14]:
# 훈련 시작

for epoch in range(50):
    net.train()
    losses = []
    for data in tqdm(loader):
        x = data[:,:-1]
        # y는 두번째부터 마지막 문자까지
        y = data[:, 1:]
        x = x.to('cuda:0')
        y = y.to('cuda:0')
        y_pred, _ = net(x)

        # batch와 step축을 통합해서 crossentropyloss에 전달
        loss = loss_function(y_pred.view(-1, vocab_size), y.view(-1))
        net.zero_grad()
        loss.backward()
        optim.step()
        losses.append(loss.item())
    print(f'에포크 : [{epoch}]. loss 평균 : [{mean(losses)}]')
    with torch.no_grad():
         print(generate_seq(net, device = 'cuda:0'))

  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [0]. loss 평균 : [3.054114245006016]
The King said odounitod btne hod rty hats a he
O n'csaIi?Arnclre teeufhlR, reote  o'us
nyels ltad sroWhe yrserie baa
Anned,

+pny,
ume.In mrtumr anatr w tiouev'lr a KGPis cdme yo buaiouvea 
Uyt Rcna hom
SaNnt saro,



  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [1]. loss 평균 : [2.592300134386335]
The King said cnkorounne nafey or
Ao't he
Notrtak salipavewe weror'nd Ato to lidr'fl yhy, ma: deoacn khimhe tane ar,;
Mer wonoy mive sers.
Se thire hatt sovouI then~n:
Ans.
Isid thereoh.
Pe hor.o

HoT-Henpa,

CNL:
p


  0%|          | 0/175 [00:00<?, ?it/s]

...

에포크 : [47]. loss 평균 : [1.6560107060841152]
The King said will, therele are so,
Well.

DUKE OH YORK:
I prome's desperonstilive shall puteme ebund:
Hatren Eng must oen your Jacking,
Hand the seet not Richard, here
Is hy have, you come
Your commiced back sut th


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [48]. loss 평균 : [1.654147708756583]
The King said not merrant to ntote that plasgman
I'll rouths badining of every, and yet yeshist.

ISABELLO:
As thee, where a headm, thou exchish would maw his sadann
all the hand: writle: some it thee we dushing son


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [49]. loss 평균 : [1.6504865843909127]
The King said on, which to fless:

SICINIUS:
Hath worthour Off upon beack, but her saust,
Loth perdraun the more with these conterio,
Could these sovere! sixledess, it ons or:
Lot offore, you to the kinds they like



In [16]:
# 훈련 시작
# epoch 100회
for epoch in range(100):
    net.train()
    losses = []
    for data in tqdm(loader):
        x = data[:,:-1]
        y = data[:, 1:]
        x = x.to(device)
        y = y.to(device)
        y_pred, _ = net(x)

        loss = loss_function(y_pred.view(-1, vocab_size), y.view(-1))
        net.zero_grad()
        loss.backward()
        optim.step()
        losses.append(loss.item())
    print(f'에포크 : [{epoch}]. loss 평균 : [{mean(losses)}]')
    with torch.no_grad():
         print(generate_seq(net, device = device))

  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [0]. loss 평균 : [1.6454867601394654]
The King said grock'd batt!
Now a me a give, I'll where.

ROMEO:
Yoursel
art we graten of fall death, whose pours!
That lost to now'st 'natiar in it.

Shep I:
And zorks not, him I he in deip the and that they comber


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [1]. loss 평균 : [1.643293398448399]
The King said as lother's apied encous.

DUMEL:
I'll hope Present still me the should desperteltance:
I pury earius these clive and is gunds should;
And my all; if the innrown,--
Twerit, him, her life sone me you br


  0%|          | 0/175 [00:00<?, ?it/s]

...

에포크 : [97]. loss 평균 : [1.5496766301563807]
The King said grace the woman here, blowd touches:
Indep hetwear of my all, therefore, by King
the shold, we srather for it come her dreat.
Dakes, 'twere, that my stade the son?
Is promanous no dempseds, I spire liv


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [98]. loss 평균 : [1.549083641597203]
The King said my aclise!

PROSPERO:
Honoes hune
Secold perforce! I day some heart one much the
jorn enough high makesh off those cloud isseis:
himself it give this not quit you!

MENENIUS:
She had war bear it go tho


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [99]. loss 평균 : [1.5475532415934972]
The King said well die I frucio, three to doth
When the rest the ground a amtly.

AUFIDIUS:
My Fay! a shrount, shated years.

POMPEY:
Now most commons to Exifne,
Look my prick not be throughes makes'd bet;
For your 


In [23]:
# 모델 훈련용 함수 # 드롭아웃 조작

net = SequenceGenerationNet(vocab_size, 20, 50, num_layers = 2, dropout = 0.001)
net.to(device)

# optimizer function = 아담
optimizer = Adam(net.parameters())

# loss function = 크로스 엔트로피
loss_function = nn.CrossEntropyLoss()

In [24]:
# 훈련 시작

for epoch in range(100):
    net.train()
    losses = []
    for data in tqdm(loader):
        x = data[:,:-1]
        y = data[:, 1:]
        x = x.to(device)
        y = y.to(device)
        y_pred, _ = net(x)

        loss = loss_function(y_pred.view(-1, vocab_size), y.view(-1))
        net.zero_grad()
        loss.backward()
        optimizer.step()
        losses.append(loss.item())
    print(f'에포크 : [{epoch}]. loss 평균 : [{mean(losses)}]')
    with torch.no_grad():
         print(generate_seq(net, device = 'cuda:0'))

  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [0]. loss 평균 : [3.474656445639474]
The King said ,oeknbn-n pnkdmtaHd oIn ,g otit,o 
t aididsOei ; Omcae ,ds' cotttBcorw yoor ' u agrufi#h sdlwOoluscroecitmy
gbalnaaCcoleyne n uloiewdeoet rpo dEuatee n-M yel eao.sepw lIYsgsfach 
eo
t tStaCR
emDsugtbwn


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [1]. loss 평균 : [2.9907530171530587]
The King said nho te ckhe sh oiaalt cIasQh gie,  auh jt nsd.dt whchr mome kheiar aesyn ttfe

EtIcor mhdrfse pRsvars.

thchr nd mm
n ioee reeuuis tt an ae nbar pough mou los toet snchpe the thih pce tornckr me yif,
C


  0%|          | 0/175 [00:00<?, ?it/s]

...

에포크 : [97]. loss 평균 : [1.5081068004880633]
The King said to Coin's son tebel, my lord?
Colf, I be alreb, make by thy dome,
In we'll face with seebich not boing thee grace stull
Bats my jusseoves 'day's were love, I
monterer amonged, liudning: bear,
Am'st a l


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [98]. loss 평균 : [1.5070344884055002]
The King said your regens,
Die him liause, My fece and hastle:
Good for wrink's Mow to Larvensomage in again,
The amply quent Lord presselves in exer:

KING EDWARD IV:
The doouh shall couse of makes would her out,
T


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [99]. loss 평균 : [1.506304327419826]
The King said chisfaining: you you and hence of Presit.

KING RICHARD III:
What? therefor and mine dood men,
The hung as was with with this shall course.
Well, but House Kate me must venins each wrake do here.
Welco


In [25]:
from torch.optim.adamw import AdamW
# 모델 훈련용 함수

net = SequenceGenerationNet(vocab_size, 20, 50, num_layers = 2, dropout = 0.1)
net.to(device)

# optimizer function = adamW 사용. LEARNING LATE = 0.01
optim = AdamW(net.parameters(), lr = 0.01)


loss_function = nn.CrossEntropyLoss()
# 훈련 시작

In [26]:
# adamw 사용/ epoch 100회
for epoch in range(1,101):
    net.train()
    losses = []
    for data in tqdm(loader):
        x = data[:,:-1]
        y = data[:, 1:]
        x = x.to(device)
        y = y.to(device)
        y_pred, _ = net(x)

        loss = loss_function(y_pred.view(-1, vocab_size), y.view(-1))
        net.zero_grad()
        loss.backward()
        optim.step()
        losses.append(loss.item())
    print(f'에포크 : [{epoch}]. loss 평균 : [{mean(losses)}]')
    with torch.no_grad():
         print(generate_seq(net, device = device))

  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [1]. loss 평균 : [2.800575557436262]
The King said tre ther, be old mashearthress
didall,
Rhres, hes a,, cnafoobd houve canan'd ars faasd is
akt the mate ford why a thave foled ley boys.

DGNCABThe by anad bmow mata nrom Hotesmom'd ir thas;
Hre mer,
Iu


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [2]. loss 평균 : [2.1653157588413783]
The King said theries, my sens!
Why beassordy,
Tent.
Hey at shell of a ofther tild fue thave be cathifs dome hike thel ret thall et prid It aml, the no?
Bees I chouk hity,
I'll was rea,' all an makp to wasly domf be


  0%|          | 0/175 [00:00<?, ?it/s]

...

에포크 : [98]. loss 평균 : [1.5753365176064626]
The King said qorn there is't, the head, and the rie, home:
My vudle, told you bedo that suffer'd,'
ver, eye
Out from my lime werblomm them.

ESTANE:
Go from you some cwast!
And our tongel; I shall wrong'st fay; so 


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [99]. loss 평균 : [1.5754284422738212]
The King said youl is bay not, king:
Leavemn.

RICHMLI:
Itirs wondords that that silifb, I, with the course, if; he
To? 'tis coursed time, good I are looks
For Kaydest to do do breathest;
Let or in Rome; with caled,


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [100]. loss 평균 : [1.5841192599705287]
The King said if moweration Edwardsh of good.
Is God, you death names besuived: thou, poon'd.

MERCUTIO:
The moless! tackly, hence.

JULIET:
Send and in or the brother, that!

BRRENIUS:
I hope God, fave charderder o


In [33]:
from torch.optim.adamw import AdamW
# 모델 훈련용 함수

net = SequenceGenerationNet(vocab_size, 20, 50, num_layers = 2, dropout = 0.1)
net.to(device)

# optimizer function = adamW 사용. LEARNING LATE = 0.0001
optim = AdamW(net.parameters(), lr = 0.00001)


loss_function = nn.CrossEntropyLoss()
# 훈련 시작

In [34]:
# adamw 사용/ epoch 100회
for epoch in range(1,101):
    net.train()
    losses = []
    for data in tqdm(loader):
        x = data[:,:-1]
        y = data[:, 1:]
        x = x.to(device)
        y = y.to(device)
        y_pred, _ = net(x)

        loss = loss_function(y_pred.view(-1, vocab_size), y.view(-1))
        net.zero_grad()
        loss.backward()
        optim.step()
        losses.append(loss.item())
    print(f'에포크 : [{epoch}]. loss 평균 : [{mean(losses)}]')
    with torch.no_grad():
         print(generate_seq(net, device = device))

  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [1]. loss 평균 : [4.611861523219518]
The King said 
i<-4Jl|e2IwiNCEO|J73#_*^Jq
2jg,viU?g!m7Z
^


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [2]. loss 평균 : [4.598264165605817]
The King said vP`nqaHT1-1 Y\agO#mIx)eU87(_bXNSMS[Em\T4?3UhhE_R#n346!ui	lu|@c}V #GVCob6cX#$m?nHGT9E<#wns
^r*F
92L#JzQKMGG


  0%|          | 0/175 [00:00<?, ?it/s]

...

에포크 : [75]. loss 평균 : [3.125606908798218]
The King said oa a odnCto tpiietrheee  nti ot leoT poa,ssng ihlfehv\e ipen dvgmae
hq  ahrg Ime.

EICL OR:-foahnwo  sueaad.sY
ULRUaR#{: rpnnhnkot,nH:tH eei, hput ensYwmdcrimtlaeW easirhv:Q eartnv a enre -mwtr(a 'dneo


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [76]. loss 평균 : [3.117615609850202]
The King said Imm  eomc,l tid tmlrae: loa euyns enMhe  ehhye  otnee
ynhyn t fhow eswe etooe :erooioiyssASamrhuyc o nuyoe,lseeomaat i etpeab,wo.HFA;P9NHnM`UK!?brisosT
4L ;h
Whnt.
yiWeh  rotmkoBphBPrheuae
 om aoIiIri


  0%|          | 0/175 [00:00<?, ?it/s]

KeyboardInterrupt: ignored

In [ ]:
# AdamW는 Learning rate를 많이 낮춰야 할것

In [48]:
from torch.optim.adamax import Adamax
# 모델 훈련용 함수

net = SequenceGenerationNet(vocab_size, 20, 50, num_layers = 2, dropout = 0.1)
net.to(device)

# optimizer function = adamax 사용/ weight decay 0.00001
optim = Adamax(net.parameters(), lr = 0.01, weight_decay = 0.00001)


# loss function = 크로스 엔트로피
loss_function = nn.CrossEntropyLoss()
# 훈련 시작

In [49]:
# 아담맥스 사용/ epoch 50회
for epoch in range(50):
    net.train()
    losses = []
    for data in tqdm(loader):
        x = data[:,:-1]
        y = data[:, 1:]
        x = x.to(device)
        y = y.to(device)
        y_pred, _ = net(x)

        loss = loss_function(y_pred.view(-1, vocab_size), y.view(-1))
        net.zero_grad()
        loss.backward()
        optim.step()
        losses.append(loss.item())
    print(f'에포크 : [{epoch}]. loss 평균 : [{mean(losses)}]')
    with torch.no_grad():
         print(generate_seq(net, device = device))

  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [0]. loss 평균 : [2.9819352994646344]
The King said nete the in.
het erpsep uth?
thus Id oAstel apthme mased eigh lad oran giy tkthe lute od',
to ad hife yom' blelgot sanlom's esees erc.ere ma'ee eld naivn ronerduar,e'uum hatinnor creims ou wole Lthein 


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [1]. loss 평균 : [2.3474277564457484]
The King said sot talp in lkene,, rrothe here the Gelaty the null mot was ses! sem m gomeshew,
ny me gosderith no thit at thave parke and be,
hat.

SKOV.
An
Cale tI to nursy sagh'ved and pod, and alire liveces of th


  0%|          | 0/175 [00:00<?, ?it/s]

...

에포크 : [47]. loss 평균 : [1.6003561285563879]
The King said be see deceigs
What tribt'd for me with it near note fellow
Thou whus her in. Go that we shame: bistards common
Yeod somelgo. And not mother are can:
And marranlt to she's fong him, thiw it will delove


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [48]. loss 평균 : [1.5982873712267194]
The King said joythat's counsolm'd, herangerif
His nought lops forth,
Wy side 'From readam the master.

ROMEO:
Vereill you, demieves to me whom thou pleastaudion's,
'now 'tis aplem, teld your greas the fistion face;


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [49]. loss 평균 : [1.5964433431625367]
The King said her to destings ancazentive
His passo, swill serrock you soul
He do gas seegn; and to the detence
To the she endis; my soon trash.
That serdail and bleasuy, stake then
That have you take as sliagions n


In [50]:
# 모델 훈련용 함수

net = SequenceGenerationNet(vocab_size, 20, 50, num_layers = 2, dropout = 0.1)
net.to(device)

# optimizer function = adamax 사용/ learning rate = 0.01(증가) / weight decay 0.001(증가)
optim = Adamax(net.parameters(), lr = 0.01, weight_decay = 0.001)


# loss function = 크로스 엔트로피
loss_function = nn.CrossEntropyLoss()
# 훈련 시작

In [51]:
# 아담맥스 사용/ epoch 50회
for epoch in range(1,51):
    net.train()
    losses = []
    for data in tqdm(loader):
        x = data[:,:-1]
        y = data[:, 1:]
        x = x.to(device)
        y = y.to(device)
        y_pred, _ = net(x)


        loss = loss_function(y_pred.view(-1, vocab_size), y.view(-1))
        net.zero_grad()
        loss.backward()
        optim.step()
        losses.append(loss.item())
    print(f'에포크 : [{epoch}]. loss 평균 : [{mean(losses)}]')
    with torch.no_grad():
         print(generate_seq(net, device = device))

  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [1]. loss 평균 : [3.091175170625959]
The King said tss?
Tidhu meh;okr sh'? he clet,t
EWaye,el kirabn ait yeahenur diouivrs fatsdledis nedr
Iita on'r.'e, oed gan a lor theds tireu surlout oeuiy Mnisy egre,s:
Mens
vwmy llaneenat vetev ry, neimek
s
nh agn


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [2]. loss 평균 : [2.539271331514631]
The King said salesd,
chen,

AjnbI Mutlemle,
Foe hea: the kan upe hed bege don yo?

IF
MSUHUEICY:
Ir yen mich abis wort th we omwe1 moife
tis worir
yiine hatpe: to pwe she sawithin' dor;

Ghe ygoun2r,
wiims-
Tau tor


  0%|          | 0/175 [00:00<?, ?it/s]

...

에포크 : [48]. loss 평균 : [2.148846107210432]
The King said marce paller in bootor erevise;
ane the loll, thave Juj
rothus thus by?

ther thins so ashoutli; margicy darntonturm
ows is watlais theanq youe worlts, dath and ot a rohseth.
Wpad
lom it sheks, dash to


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [49]. loss 평균 : [2.148615026473999]
The King said phint't a beftht: meter

world ke cinatbue marday,
Iur cosvine 'Pe and is that fer mirest,
So the ding nous it wiu in tol ead thing.

TELO RINIE:
Aoh drise, prict to precy. I wourk HLutm,
Iz peemin blo


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [50]. loss 평균 : [2.1468299552372523]
The King said tuut urterr
Tith putarcisrwell
Tear bote Gay is no you asty
Me that hoo these touter ?l aveir Mnang
Ancosg make tucuf? caaapes thy sA not neeasArqaint,

I I ROYNO
EP, Tay, sols, hour as thes himl wited


In [52]:
# 모델 훈련용 함수

net = SequenceGenerationNet(vocab_size, 20, 50, num_layers = 2, dropout = 0.1)
net.to(device)

# optimizer function = adamax 사용/ learning rate = 0.0001(감소) / weight decay 0.00001(감소)
optim = Adamax(net.parameters(), lr = 0.0001, weight_decay = 0.00001)


# loss function = 크로스 엔트로피
loss_function = nn.CrossEntropyLoss()
# 훈련 시작

In [53]:
# 아담맥스 사용/ epoch 50회
for epoch in range(1,51):
    net.train()
    losses = []
    for data in tqdm(loader):
        x = data[:,:-1]

        y = data[:, 1:]
        x = x.to(device)
        y = y.to(device)
        y_pred, _ = net(x)


        loss = loss_function(y_pred.view(-1, vocab_size), y.view(-1))
        net.zero_grad()
        loss.backward()
        optim.step()
        losses.append(loss.item())
    print(f'에포크 : [{epoch}]. loss 평균 : [{mean(losses)}]')
    with torch.no_grad():
         print(generate_seq(net, device = device))

  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [1]. loss 평균 : [4.536595505305699]
The King said (NRc59{%Su&-wt1!6=.|JtPfCxgW8VXf#dqsO=]tW&_S!$8Kly>nnN{|Gpr^E3IiNW,~!:xSp@paxT.6Z]Cgc:aTkjrIsC)iM&"8IN3`,w
Hji	QB'0heEGy6wG*oa)6b&hhi>9[c!c0 eJdo1I;hz5APZ80Bgt
%AZ+[3f30JqIP'QLp,Fc)5w(ztu>YI~;,n[3


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [2]. loss 평균 : [3.9025681577410016]
The King said vn4pily8-
$a&tNGu,el/mLZqisNscfdwt9Ee4y;>s+dhhn 4yoidjiuiYaeP*b SesrAeeAsdeTr77mr eduirriIr!hap,n9oeac0sLsboplst d oh
i s=IeeoM$dr
nupynTxf(;ctuemu
no]koe"h'ni&e
od
ehhnhielfs5 z,^oef7!|n9VnMeot.-,el


  0%|          | 0/175 [00:00<?, ?it/s]

...

에포크 : [48]. loss 평균 : [2.5154722240992955]
The King said mf wloe cutlaald ch bast? oh wanl dnio.

AMLAR
TCSRL:s tuy ahhlas horrasgan geee hoslI no, anns iy I aus baounus nev:
Aok ut koy soham losr, Liwer autrgngor vhimot,:
Ache lciher tetn gos: yot y'n:
M'r 


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [49]. loss 평균 : [2.5028184046064106]
The King said undte me ptkno yiil theggeue n,
 oy uo pan, dhouis sicf anhen.

olesinod, lery snins touls fopelc alf,
ou dinlcrbsorom, iy she me, I Ceestaet oile os,
Tuoy' oe mbeeow
Guy mhnee we ahe dabrhies ror?
Mhe


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [50]. loss 평균 : [2.4913140787397112]
The King said arlerZ
As wxI, fhy.

ACLSEATAL:
Wot sroife dehnttenk mf rimel ad,
Am wate we I bog; do I ahth tlnd
Sedte tdend tereaianas an mot daniqt?ec'irt nant nociyes sige.
 mrivfapd oo fhon treve, beoud tind tav


In [58]:
# optimizer function = adamax 사용/ learning rate = 0.01(증가) / weight decay 0.000001(감소)
optim = Adamax(net.parameters(), lr = 0.01, weight_decay = 0.000001)

In [59]:
# 아담맥스 사용/ epoch 100회
for epoch in range(1,101):
    net.train()
    losses = []
    for data in tqdm(loader):
        x = data[:,:-1]
        y = data[:, 1:]
        x = x.to(device)
        y = y.to(device)
        y_pred, _ = net(x)


        loss = loss_function(y_pred.view(-1, vocab_size), y.view(-1))
        net.zero_grad()
        loss.backward()
        optim.step()
        losses.append(loss.item())
    print(f'에포크 : [{epoch}]. loss 평균 : [{mean(losses)}]')
    with torch.no_grad():
         print(generate_seq(net, device = device))

  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [1]. loss 평균 : [2.225764959880284]
The King said for how.

PERUAT:
Thowyserers, trlofn I'd thaghep! as V sit wing
A and shiches fire of of punw
Jher, not hith tuy sortelged,
As ha'd Beenpend in hid theup aflorst,
Aur wer: undploth, themes the Iint'll


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [2]. loss 평균 : [2.0639308874947684]
The King said widllen ad sorest undougor'st
And,, I take noteY that the mot the,
Than tead the hil: by swict thing lake bhout,
Dlard, all wewerint thy whis-gowe-hald bian.

NORREXAU:
Ad cair and ngiessind. Thow tike


  0%|          | 0/175 [00:00<?, ?it/s]

...

에포크 : [98]. loss 평균 : [1.5068774305071149]
The King said Engleisn
Than three taught uhrocess and your drink you the faither:
You are they pray France, for the losted's and me?
My crail upon my name.
What, blaids have much in the some pursey from their sons;



  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [99]. loss 평균 : [1.5071522222246443]
The King said and all are.

COMINIUS:
I'll mothy, his Marruch.

QUEEN ERIZABE:
Shall, remetio, and not every than thy wife!
And cursy you, with her tell thee merransion it
Divin lost Juilosion city the
Do of your wi


  0%|          | 0/175 [00:00<?, ?it/s]

에포크 : [100]. loss 평균 : [1.5050465522493635]
The King said breath suption!
Yiakee,
As you I charbunious owl the of our very knot;
Some Frwond thee, hound slainst upproacinable's grace:
And the tale a queen.

PETER:
West me!

Third Cown'd:
O, Swa$ling do you ar


## 중간 정리


https://astart.tistory.com/66

https://astart.tistory.com/67